Основаная задача - **построить хорошую тематическую модель с интерпретируемыми топиками с помощью LDA в gensim и NMF в sklearn**.


1) сделайте нормализацию (если pymorphy2 работает долго используйте mystem или попробуйте установить быструю версию - `pip install pymorphy2[fast]`, можно использовать какой-то другой токенизатор); 

2) добавьте нграммы (в тетрадке есть закомменченая ячейка с Phrases,  можно также попробовать другие способы построить нграммы); 

3) сделайте хороший словарь (отфильтруйте слишком частотные и редкие слова, попробуйте удалить стоп-слова); 

4) постройте несколько LDA моделей (переберите количество тем, можете поменять alpha, passes), если получаются плохие темы, поработайте дополнительно над предобработкой и словарем; 

5) для самой хорошей модели в отдельной ячейке напечатайте 3 хороших (на ваш вкус) темы;

6) между словарем и обучением модели добавьте tfidf (`tfidf = gensim.models.TfidfModel(corpus, id2word=dictionary); corpus = tfidf[corpus]`);

7) повторите пункт 4 на преобразованном корпусе (подбирайте параметры, ориентируясь на качество, а не на результаты, которые вы получали без tfidf);

8) в отдельной ячейке сравните лучшую модель без tfidf и лучшую модель с tfidf (приведите несколько тем, которые стали лучше или хуже, или которых раньше вообще не было; можно привести значения перплексии и когерентности для обеих моделей)

9) проделайте такие же действия для NMF (образец в конце тетрадки), для построения словаря воспользуйтесь возможностями Count или Tfidf Vectorizer (попробуйте другие значение max_features, min_df, max_df, сделайте нграмы через ngram_range, если хватает памяти), попробуйте такие же количества тем

10) в отдельной ячейки напечатайте темы лучшей NMF модели, сравните их с теми, что получились в LDA.

Сохраните тетрадку с экспериментами и положите её на гитхаб, ссылку на неё укажите в форме.

**Оцениваться будут главным образом пункты 5, 8 и 10. (2, 3, 2 баллов соответственно). Чтобы заработать остальные 3 балла, нужно хотя бы немного изменить мой код на промежуточных этапах (добавить что-то, указать другие параметры и т.д). **


Острожнее интерпретируйте полученные результаты. Если один алгоритм сработал хорошо в этом задании - не значит, что он всегда будет хорошо работать, и наоборот.

In [2]:
import gensim
import json
import re
import pandas as pd
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from pymorphy2 import MorphAnalyzer
import pyLDAvis.gensim
import string
from collections import Counter
import warnings
warnings.filterwarnings("ignore")
from IPython.display import Image
from IPython.core.display import HTML 
morph = MorphAnalyzer()

## 1) сделайте нормализацию (если pymorphy2 работает долго используйте mystem или попробуйте установить быструю версию - `pip install pymorphy2[fast]`, можно использовать какой-то другой токенизатор);  

In [3]:
stops = set(stopwords.words('russian'))

# чтобы быстрее нормализовать тексты, создадим словарь всех словоформ
# нормазуем каждую 1 раз и положим в словарь
# затем пройдем по текстам и сопоставим каждой словоформе её нормальную форму

def opt_normalize(texts, top=None):
    uniq = Counter()
    for text in texts:
        uniq.update(text)
    
    norm_uniq = {word:morph.parse(word)[0].normal_form for word, _ in uniq.most_common(top)}
    
    norm_texts = []
    for text in texts:
        
        norm_words = [norm_uniq.get(word) for word in text]
        norm_words = [word for word in norm_words if word and word not in stops]
        norm_texts.append(norm_words)
        
    return norm_texts

def tokenize(text):
    words = [word.strip(string.punctuation) for word in text.split()]
    words = [word for word in words if word]
    
    return words

In [4]:
texts = open('wiki_data.txt').read().splitlines()[:10000]

In [5]:
len(texts)

10000

In [6]:
texts = opt_normalize([tokenize(text.lower()) for text in texts], 30000)

In [7]:
texts[:3]

[['нижегородский',
  '—',
  'сельский',
  'посёлок',
  'район',
  'нижегородский',
  'область',
  'входить',
  'состав',
  'расположить',
  '12,5',
  'километр',
  'юг',
  'село',
  '1',
  'километр',
  'запасть',
  'город',
  'право',
  'берег',
  'река',
  'правый',
  'приток',
  'река',
  'сатис',
  'окружить',
  'смешанный',
  'леса',
  'соединить',
  'дорогой',
  'посёлок',
  '1,5',
  'километр',
  'дорога',
  'посёлок',
  'сатис',
  '3,5',
  'километр',
  'название',
  'являться',
  'сугубо',
  'официальный',
  'местный',
  'население',
  'использовать',
  'исключительно',
  'название',
  '—',
  'употребляться',
  'языковой',
  'оборот',
  'ранее',
  'использовать',
  'название',
  '—',
  '1920-ха',
  'год',
  'переселенец',
  'соседний',
  'село',
  'аламасовый',
  'расположить',
  'соответственно',
  '8',
  '14',
  'километр',
  'запасть',
  'посёлок',
  'жить',
  'рабочий',
  'совхоз',
  'центр',
  'посёлок',
  'сатис',
  'возле',
  'посёлок',
  'расположить',
  'активно',
  '

## 2) добавьте нграммы (в тетрадке есть закомменченая ячейка с Phrases,  можно также попробовать другие способы построить нграммы); 

In [8]:
# для нграммов
ph = gensim.models.Phrases(texts, scoring='npmi', threshold=0.4) # threshold можно подбирать
p = gensim.models.phrases.Phraser(ph)
ngrammed_texts = p[texts]

## 3) сделайте хороший словарь (отфильтруйте слишком частотные и редкие слова, попробуйте удалить стоп-слова); 

In [9]:
dictinary = gensim.corpora.Dictionary(texts)

In [10]:
dictinary.filter_extremes(no_above=0.2, no_below=20)
dictinary.compactify()

In [11]:
print(dictinary)

Dictionary(5770 unique tokens: ['1', '1,2', '1,5', '12', '14']...)


Преобразуем наши тексты в мешки слов. 

In [13]:
corpus = [dictinary.doc2bow(text) for text in texts]

## 6) между словарем и обучением модели добавьте tfidf (`tfidf = gensim.models.TfidfModel(corpus, id2word=dictionary); corpus = tfidf[corpus]`);

In [15]:
tfidf = gensim.models.TfidfModel(corpus, id2word=dictinary)
corpus_tfidf = tfidf[corpus]

## 4) постройте несколько LDA моделей (переберите количество тем, можете поменять alpha, passes), если получаются плохие темы, поработайте дополнительно над предобработкой и словарем; 

In [16]:
?gensim.models.LdaMulticore

Основные это num_topics, alpha, eta и passes. 

**num_topics** - это количество тем. Это основной параметр и настраивать его проще всего. Обычно 200 оптимальное значение. Можно поставить поменьше, если тексты не очень разнообразные или хочется уменьшить время обучения.

**alpha** и **eta** - параметры, которые влияют на разреженность распределения документы-темы и темы-слова. У alpha есть значения "asymmetric" и "auto", которые можно попробовать (по умолчанию стоит "symmetric", т.е. не разреженное). Eta можно задать каким-то числом или самому сделать изначальное распределение слов по темам. НО настраивать эти параметры сложно и непонятно и вообще лучше надеяться, что по умолчанию все заработает.

**passes** - задает количество проходов по данным. Чем больше, тем лучше сойдется модель, но обучаться будет дольше.

In [22]:
lda_1 = gensim.models.LdaMulticore(corpus, num_topics=100, id2word=dictinary, passes=10)

In [26]:
lda_1.print_topics()

[(73,
  '0.060*"улица" + 0.022*"город" + 0.018*"дом" + 0.013*"площадь" + 0.012*"название" + 0.008*"век" + 0.007*"№" + 0.007*"москва" + 0.007*"часть" + 0.007*"проходить"'),
 (51,
  '0.035*"корабль" + 0.025*"флот" + 0.018*"лодка" + 0.017*"крейсер" + 0.010*"подводный" + 0.010*"японский" + 0.009*"китайский" + 0.008*"эскадра" + 0.007*"адмирал" + 0.006*"морской"'),
 (81,
  '0.015*"партия" + 0.012*"страна" + 0.011*"президент" + 0.011*"правительство" + 0.011*"политический" + 0.008*"власть" + 0.007*"министр" + 0.007*"национальный" + 0.007*"государство" + 0.006*"военный"'),
 (80,
  '0.019*"военный" + 0.017*"армия" + 0.015*"начальник" + 0.014*"война" + 0.013*"август" + 0.013*"командир" + 0.012*"штаб" + 0.011*"назначить" + 0.010*"должность" + 0.010*"октябрь"'),
 (57,
  '0.029*"король" + 0.028*"граф" + 0.027*"сын" + 0.020*"i" + 0.020*"де" + 0.020*"ii" + 0.014*"брат" + 0.013*"дочь" + 0.013*"смерть" + 0.011*"графство"'),
 (37,
  '0.020*"компания" + 0.009*"получить" + 0.009*"шоу" + 0.008*"октябрь" + 0

In [23]:
lda_2 = gensim.models.LdaMulticore(corpus, num_topics=200, id2word=dictinary, passes=10)

In [27]:
lda_2.print_topics()

[(106,
  '0.025*"водохранилище" + 0.014*"гэс" + 0.010*"вид" + 0.010*"род" + 0.010*"гимн" + 0.010*"африка" + 0.008*"формировать" + 0.008*"часть" + 0.008*"около" + 0.007*"78"'),
 (125,
  '0.081*"коммуна" + 0.036*"норвегия" + 0.031*"означать" + 0.027*"аэропорт" + 0.023*"поезд" + 0.018*"вагон" + 0.017*"норвежский" + 0.015*"название" + 0.013*"мочь" + 0.012*"тип"'),
 (137,
  '0.041*"лига" + 0.033*"прыжок" + 0.020*"адам" + 0.018*"команда" + 0.016*"результат" + 0.012*"предварительный" + 0.011*"полуфинал" + 0.010*"6" + 0.010*"спортсмен" + 0.010*"получить"'),
 (60,
  '0.017*"суд" + 0.012*"союз" + 0.010*"фестиваль" + 0.010*"литературный" + 0.008*"международный" + 0.008*"инструмент" + 0.008*"гитлер" + 0.008*"музыкальный" + 0.007*"писатель" + 0.007*"имя"'),
 (182,
  '0.015*"ирландия" + 0.014*"матч" + 0.011*"победа" + 0.009*"команда" + 0.007*"против" + 0.007*"сборный" + 0.006*"однако" + 0.006*"ирландский" + 0.006*"новый" + 0.006*"последний"'),
 (32,
  '0.128*"уезд" + 0.040*"городской" + 0.036*"округ

In [24]:
lda_3 = gensim.models.LdaMulticore(corpus, num_topics=100, id2word=dictinary, passes=20)

In [28]:
lda_3.print_topics()

[(70,
  '0.087*"суд" + 0.059*"библиотека" + 0.025*"судебный" + 0.023*"верховный" + 0.016*"дело" + 0.015*"судья" + 0.013*"решение" + 0.012*"№" + 0.010*"тамбовский" + 0.008*"фонд"'),
 (20,
  '0.025*"музыкальный" + 0.025*"азербайджанский" + 0.022*"место" + 0.021*"1-е" + 0.020*"инструмент" + 0.019*"музыка" + 0.015*"оркестр" + 0.014*"участник" + 0.014*"баку" + 0.014*"международный"'),
 (48,
  '0.061*"наш" + 0.049*"э" + 0.020*"город" + 0.018*"римский" + 0.014*"война" + 0.013*"консул" + 0.012*"рим" + 0.011*"царь" + 0.009*"римляна" + 0.009*"войско"'),
 (47,
  '0.016*"её" + 0.008*"мочь" + 0.007*"однако" + 0.007*"жизнь" + 0.006*"имя" + 0.006*"друг" + 0.006*"самый" + 0.006*"пытаться" + 0.005*"день" + 0.005*"должный"'),
 (7,
  '0.048*"церковь" + 0.028*"храм" + 0.023*"собор" + 0.022*"епископ" + 0.020*"епархия" + 0.019*"православный" + 0.018*"монастырь" + 0.014*"святой" + 0.011*"русский" + 0.010*"церковный"'),
 (16,
  '0.020*"билет" + 0.014*"рубль" + 0.013*"коми" + 0.011*"банк" + 0.011*"банка" + 0.0

In [25]:
lda_4 = gensim.models.LdaMulticore(corpus, num_topics=200, id2word=dictinary, passes=20)

In [29]:
lda_4.print_topics()

[(125,
  '0.037*"дата" + 0.034*"список" + 0.029*"константиновский" + 0.028*"орден" + 0.017*"гражданство" + 0.016*"кавалер" + 0.015*"мощь" + 0.014*"полный" + 0.013*"латвия" + 0.013*"слава"'),
 (60,
  '0.024*"сша" + 0.021*"компания" + 0.018*"военный" + 0.015*"американский" + 0.015*"китайский" + 0.007*"должность" + 0.007*"главный" + 0.007*"китай" + 0.006*"государство" + 0.006*"война"'),
 (118,
  '0.110*"музей" + 0.031*"искусство" + 0.023*"художник" + 0.017*"художественный" + 0.015*"коллекция" + 0.015*"произведение" + 0.013*"галерея" + 0.012*"выставка" + 0.011*"век" + 0.011*"картина"'),
 (5,
  '0.061*"республика" + 0.043*"российский" + 0.036*"ссср" + 0.021*"федерация" + 0.017*"1992" + 0.015*"советский" + 0.014*"1993" + 0.013*"россия" + 0.013*"владимир" + 0.011*"2016"'),
 (113,
  '0.024*"вид" + 0.010*"мочь" + 0.009*"около" + 0.009*"иметь" + 0.009*"являться" + 0.008*"тело" + 0.008*"некоторый" + 0.007*"животное" + 0.007*"очень" + 0.007*"часть"'),
 (196,
  '0.092*"хутор" + 0.046*"посёлок" + 0.

Ещё есть штука для визуализации.

### Файл ноутбука получился слишком большим, поэтому я оставила визуализации только самых удачных моделей

In [30]:
pyLDAvis.enable_notebook()

In [ ]:
pyLDAvis.gensim.prepare(lda_1, corpus, dictinary)

In [32]:
pyLDAvis.enable_notebook()

In [ ]:
pyLDAvis.gensim.prepare(lda_2, corpus, dictinary)

In [34]:
pyLDAvis.enable_notebook()

In [35]:
pyLDAvis.gensim.prepare(lda_3, corpus, dictinary)

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
57     0.071656 -0.072562       1        1  4.044939
47    -0.134671 -0.141767       2        1  3.995971
81    -0.159020 -0.080399       3        1  3.376910
6      0.204997 -0.081270       4        1  2.923940
72     0.127189  0.212212       5        1  2.906678
...         ...       ...     ...      ...       ...
39     0.054183 -0.098102      96        1  0.138318
85    -0.053691  0.032083      97        1  0.120077
68    -0.051771 -0.007093      98        1  0.105044
49     0.015685 -0.002773      99        1  0.103989
14     0.033756  0.000183     100        1  0.094875

[100 rows x 5 columns], topic_info=             Term         Freq        Total  Category  logprob  loglift
4795  житомирский  3408.000000  3408.000000   Default  30.0000  30.0000
211          игра  3925.000000  3925.000000   Default  29.0000  29.0000
1915  олимпийский  2434.000000  2434.000000   Default  28.0000  28.0000
463         сесть  2551.000000  2551.000000   Default  27.0000  27.0000
593          уезд  1799.000000  1799.000000   Default  26.0000  26.0000
...           ...          ...          ...       ...      ...      ...
421      занимать     6.654032  1950.885254  Topic100  -5.0412   1.2796
213         иметь     6.493551  2629.413086  Topic100  -5.0657   0.9567
617             5     6.117174  1235.973022  Topic100  -5.1254   1.6519
1291    александр     5.805545   852.284790  Topic100  -5.1776   1.9713
745         место     6.007825  2683.289062  Topic100  -5.1434   0.8586

[5377 rows x 6 columns], token_table=      Topic      Freq Term
term                      
4235      5  0.192870    0
4235      9  0.038574    0
4235     19  0.012858    0
4235     29  0.038574    0
4235     35  0.012858    0
...     ...       ...  ...
449      85  0.003063    №
449      87  0.001021    №
449      91  0.005105    №
449      92  0.003063    №
449      93  0.005105    №

[57544 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[58, 48, 82, 7, 73, 5, 100, 23, 93, 45, 18, 99, 65, 39, 78, 59, 52, 26, 46, 22, 12, 68, 88, 10, 16, 89, 84, 95, 64, 60, 56, 66, 25, 8, 37, 2, 80, 85, 33, 42, 70, 54, 90, 9, 13, 49, 44, 77, 24, 79, 97, 34, 19, 27, 61, 14, 55, 3, 83, 31, 38, 74, 4, 30, 32, 98, 36, 76, 92, 1, 62, 51, 21, 63, 75, 17, 41, 43, 47, 87, 11, 71, 35, 67, 94, 20, 29, 81, 57, 96, 91, 72, 28, 53, 6, 40, 86, 69, 50, 15])

In [36]:
pyLDAvis.enable_notebook()

In [ ]:
pyLDAvis.gensim.prepare(lda_4, corpus, dictinary)

На графике должно быть как можно меньше пересекающихся кружков (т.е. темы состоят из разных слов), а сами кружки не должны быть огромными (скорее всего такую тему можно разбить на несколько поменьше).

Можно посмотреть метрики.

**Перплексия** показывает насколько хороше моделируется корпус. Чем ближе к нулю, тем лучше. Можно использовать, чтобы настраивать количество проходов по корпусу (когда перестало улучшаться, то можно останавливаться).

Ещё есть **когерентность**. Она численно оценивает качество тем (проверяется, что темы состоят из разных слов и что в теме есть топ тематических слов). Чем выше, тем лучше.

Но все эти числа вспомогательны! Главные критерии качества модели: интерпретируемость и понятность тем (т.е. нужно глазами смотреть на каждую тему), а также польза для практической задачи, которую вы пытаетесь решить.

In [38]:
import numpy as np

In [42]:
def metrics(lda, corpus, texts):
    perp = lda.log_perplexity(corpus[:1000])
    
    topics = []
    for topic_id, topic in lda.show_topics(num_topics=100, formatted=False):
        topic = [word for word, _ in topic]
        topics.append(topic)
    
    coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')
    coh = coherence_model_lda.get_coherence()
    print(f"Перплексия {perp}, когерентность {coh}")

In [43]:
metrics(lda_1, corpus, texts)

Перплексия -13.743944876179347, когерентность 0.5541582094505566


In [44]:
metrics(lda_2, corpus, texts)

Перплексия -18.825592478138244, когерентность 0.5391961141856576


In [45]:
metrics(lda_3, corpus, texts)

Перплексия -11.249107894828825, когерентность 0.5814369616350556


In [46]:
metrics(lda_4, corpus, texts)

Перплексия -13.680708321644431, когерентность 0.5276739472349832


По темам и визуаилзации мне тоже больше третья модель понравилась (и по метрикам она лучше). Примеры трех тем:

In [48]:
lda_3.print_topic(7) # религия или даже уже "церковь"

'0.048*"церковь" + 0.028*"храм" + 0.023*"собор" + 0.022*"епископ" + 0.020*"епархия" + 0.019*"православный" + 0.018*"монастырь" + 0.014*"святой" + 0.011*"русский" + 0.010*"церковный"'

In [52]:
lda_3.print_topic(24) # ТВ, сериалы

'0.027*"сериал" + 0.023*"доктор" + 0.019*"серия" + 0.018*"сезон" + 0.017*"эпизод" + 0.016*"роль" + 0.011*"фильм" + 0.009*"персонаж" + 0.008*"смит" + 0.008*"канал"'

In [51]:
lda_3.print_topic(83) # Образование

'0.060*"университет" + 0.017*"наука" + 0.017*"школа" + 0.014*"профессор" + 0.014*"факультет" + 0.012*"образование" + 0.011*"научный" + 0.011*"институт" + 0.009*"кафедра" + 0.009*"студент"'

## 7) повторите пункт 4 на преобразованном корпусе (подбирайте параметры, ориентируясь на качество, а не на результаты, которые вы получали без tfidf);

In [53]:
lda_5 = gensim.models.LdaMulticore(corpus_tfidf, num_topics=100, id2word=dictinary, passes=10)

In [54]:
lda_5.print_topics()

[(3,
  '0.147*"житомирский" + 0.057*"код" + 0.055*"телефонный" + 0.055*"р-наш" + 0.055*"украина" + 0.051*"сесть" + 0.051*"2001" + 0.050*"площадь" + 0.050*"тело" + 0.048*"занимать"'),
 (11,
  '0.161*"перепись" + 0.137*"ул" + 0.107*"области.############население" + 0.097*"индекс" + 0.064*"романовский" + 0.027*"4146" + 0.020*"центральный" + 0.019*"полюс" + 0.008*"бургундия" + 0.008*"1890"'),
 (68,
  '0.042*"комплект" + 0.027*"оснастить" + 0.024*"ирина" + 0.024*"языковой" + 0.021*"поставка" + 0.019*"ёмкость" + 0.018*"ан" + 0.016*"ночное" + 0.015*"рана" + 0.014*"модель"'),
 (26,
  '0.365*"новоград-волынский" + 0.051*"аргентина" + 0.028*"космический" + 0.028*"провинция" + 0.015*"секция" + 0.013*"включать" + 0.013*"институт" + 0.013*"2010" + 0.011*"национальный" + 0.009*"чайковский"'),
 (56,
  '0.048*"виконт" + 0.038*"копия" + 0.020*"голландский" + 0.020*"дик" + 0.018*"music" + 0.017*"1861" + 0.016*"оптический" + 0.016*"фасад" + 0.015*"купол" + 0.013*"унаследовать"'),
 (67,
  '0.116*"монреаль

In [55]:
lda_6 = gensim.models.LdaMulticore(corpus_tfidf, num_topics=100, id2word=dictinary, passes=20)

In [56]:
lda_6.print_topics()

[(13,
  '0.048*"улица" + 0.019*"храм" + 0.013*"церковь" + 0.012*"москва" + 0.012*"здание" + 0.010*"экспедиция" + 0.010*"ссср" + 0.009*"бывший" + 0.009*"различный" + 0.008*"литовский"'),
 (70,
  '0.063*"мексика" + 0.054*"мехико" + 0.031*"боливия" + 0.026*"тайвань" + 0.025*"недалеко" + 0.025*"марка" + 0.022*"автодорога" + 0.018*"прокурор" + 0.018*"марокко" + 0.015*"57"'),
 (64,
  '0.035*"километр" + 0.030*"река" + 0.023*"расположить" + 0.020*"берег" + 0.018*"расстояние" + 0.018*"сельский" + 0.017*"посёлок" + 0.016*"село" + 0.016*"озеро" + 0.016*"дорога"'),
 (84,
  '0.024*"профессор" + 0.023*"наука" + 0.020*"филиппина" + 0.019*"институт" + 0.016*"академия" + 0.014*"кафедра" + 0.014*"университет" + 0.014*"александр" + 0.013*"научный" + 0.013*"доктор"'),
 (56,
  '0.076*"0" + 0.035*"ракета" + 0.023*"иванов" + 0.020*"цепь" + 0.018*"схема" + 0.017*"настройка" + 0.016*"1906" + 0.015*"список" + 0.014*"эффект" + 0.010*"установка"'),
 (8,
  '0.046*"uss" + 0.046*"эсминец" + 0.032*"строить" + 0.028*

In [57]:
lda_7 = gensim.models.LdaMulticore(corpus_tfidf, num_topics=200, id2word=dictinary, passes=20)

In [58]:
lda_7.print_topics()

[(1,
  '0.154*"буква" + 0.105*"информация" + 0.099*"использование" + 0.075*"вариант" + 0.065*"таблица" + 0.065*"сообщение" + 0.044*"ключ" + 0.035*"сведение" + 0.026*"машина" + 0.021*"настройка"'),
 (94,
  '0.000*"57" + 0.000*"франк" + 0.000*"1-я" + 0.000*"шотландия" + 0.000*"обитание" + 0.000*"дошлый" + 0.000*"рок" + 0.000*"жак" + 0.000*"британия" + 0.000*"new"'),
 (95,
  '0.000*"57" + 0.000*"франк" + 0.000*"1-я" + 0.000*"шотландия" + 0.000*"обитание" + 0.000*"дошлый" + 0.000*"рок" + 0.000*"жак" + 0.000*"британия" + 0.000*"new"'),
 (188,
  '0.000*"57" + 0.000*"франк" + 0.000*"1-я" + 0.000*"шотландия" + 0.000*"обитание" + 0.000*"дошлый" + 0.000*"рок" + 0.000*"жак" + 0.000*"британия" + 0.000*"new"'),
 (75,
  '0.000*"57" + 0.000*"франк" + 0.000*"1-я" + 0.000*"шотландия" + 0.000*"обитание" + 0.000*"дошлый" + 0.000*"рок" + 0.000*"жак" + 0.000*"британия" + 0.000*"new"'),
 (134,
  '0.000*"57" + 0.000*"франк" + 0.000*"1-я" + 0.000*"шотландия" + 0.000*"обитание" + 0.000*"дошлый" + 0.000*"рок" +

In [60]:
lda_8 = gensim.models.LdaModel(corpus_tfidf, num_topics=100, id2word=dictinary, passes=20, alpha='auto')

In [61]:
lda_8.print_topics()

[(67,
  '0.000*"57" + 0.000*"франк" + 0.000*"1-я" + 0.000*"шотландия" + 0.000*"обитание" + 0.000*"дошлый" + 0.000*"рок" + 0.000*"жак" + 0.000*"британия" + 0.000*"new"'),
 (0,
  '0.000*"ла" + 0.000*"британия" + 0.000*"57" + 0.000*"10-ть" + 0.000*"1-я" + 0.000*"шотландия" + 0.000*"обитание" + 0.000*"дошлый" + 0.000*"рок" + 0.000*"жак"'),
 (44,
  '0.048*"рубль" + 0.042*"91" + 0.014*"«" + 0.008*"ставиться" + 0.007*"доход" + 0.000*"недолго" + 0.000*"new" + 0.000*"британия" + 0.000*"рок" + 0.000*"тайна"'),
 (60,
  '0.093*"тринадцать" + 0.036*"смит" + 0.000*"дошлый" + 0.000*"британия" + 0.000*"жак" + 0.000*"рок" + 0.000*"57" + 0.000*"обитание" + 0.000*"тайна" + 0.000*"шотландия"'),
 (50,
  '0.048*"коллекция" + 0.030*"особняк" + 0.025*"вызов" + 0.012*"авторство" + 0.011*"мечтать" + 0.000*"замечать" + 0.000*"защищать" + 0.000*"фотография" + 0.000*"шотландия" + 0.000*"обитание"'),
 (4,
  '0.125*"люксембург" + 0.050*"for" + 0.000*"68" + 0.000*"каменный" + 0.000*"сооружение" + 0.000*"рок" + 0.000*

In [62]:
pyLDAvis.enable_notebook()

In [63]:
pyLDAvis.gensim.prepare(lda_5, corpus_tfidf, dictinary)

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
74    -0.137927  0.101034       1        1  22.511215
30    -0.201266  0.017861       2        1   6.584486
36    -0.157363  0.096916       3        1   5.991755
3     -0.313910 -0.150902       4        1   4.800183
64    -0.230773  0.177758       5        1   4.183399
...         ...       ...     ...      ...        ...
44     0.089594  0.012031      96        1   0.188811
22     0.087605  0.011749      97        1   0.185462
2      0.098363  0.000792      98        1   0.181051
93     0.091464  0.006007      99        1   0.166493
85     0.090338  0.006885     100        1   0.161010

[100 rows x 5 columns], topic_info=             Term        Freq       Total  Category  logprob  loglift
4795  житомирский  408.000000  408.000000   Default  30.0000  30.0000
1915  олимпийский  230.000000  230.000000   Default  29.0000  29.0000
211          игра  232.000000  232.000000   Default  28.0000  28.0000
4237       индекс  147.000000  147.000000   Default  27.0000  27.0000
458      перепись  149.000000  149.000000   Default  26.0000  26.0000
...           ...         ...         ...       ...      ...      ...
1840   московский    0.037329   36.115402  Topic100  -7.8175  -0.4433
72         состав    0.039253  105.572174  Topic100  -7.7673  -1.4657
113    российский    0.037759   51.209961  Topic100  -7.8061  -0.7810
450            21    0.036838   28.990040  Topic100  -7.8308  -0.2367
566      сентябрь    0.036899   48.286789  Topic100  -7.8291  -0.7453

[4307 rows x 6 columns], token_table=      Topic      Freq Term
term                      
4235      7  0.109144    0
4235     62  0.764009    0
598       1  0.863815  000
0         1  0.240490    1
0         2  0.036073    1
...     ...       ...  ...
449       6  0.184624    №
449       7  0.026375    №
449      11  0.131874    №
449      23  0.026375    №
449      46  0.026375    №

[7321 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[75, 31, 37, 4, 65, 58, 10, 50, 56, 51, 35, 79, 95, 25, 47, 67, 17, 89, 12, 33, 48, 26, 8, 71, 43, 42, 72, 64, 52, 73, 29, 30, 44, 85, 76, 60, 81, 11, 83, 53, 96, 82, 87, 36, 6, 13, 2, 27, 46, 78, 66, 7, 88, 77, 34, 20, 98, 19, 28, 18, 61, 32, 14, 5, 80, 22, 91, 38, 55, 1, 54, 70, 15, 93, 16, 63, 69, 59, 24, 57, 90, 41, 84, 49, 74, 40, 100, 97, 9, 62, 39, 99, 92, 68, 21, 45, 23, 3, 94, 86])

In [64]:
pyLDAvis.enable_notebook()

In [ ]:
pyLDAvis.gensim.prepare(lda_6, corpus_tfidf, dictinary)

In [66]:
pyLDAvis.enable_notebook()

In [ ]:
pyLDAvis.gensim.prepare(lda_7, corpus_tfidf, dictinary)

In [68]:
pyLDAvis.enable_notebook()

In [ ]:
pyLDAvis.gensim.prepare(lda_8, corpus_tfidf, dictinary)

In [70]:
metrics(lda_5, corpus_tfidf, texts)

Перплексия -31.661404775244883, когерентность 0.4537931140055324


In [71]:
metrics(lda_6, corpus_tfidf, texts)

Перплексия -29.7407464624949, когерентность 0.46805663976903394


In [72]:
metrics(lda_7, corpus_tfidf, texts)

Перплексия -158.22246450233024, когерентность 0.4938648255134378


In [73]:
metrics(lda_8, corpus_tfidf, texts)

Перплексия -19.558114425523808, когерентность 0.4342339691569154


Темы уже подобраны значительно хуже, что видно как и по словам, так и по визуализации и метрикам. Мне кажется, что лучше всего показала себя модель lda_5

In [74]:
lda_5.print_topic(34) # Армия

'0.028*"армия" + 0.023*"дивизия" + 0.020*"командир" + 0.019*"бой" + 0.017*"фронт" + 0.017*"война" + 0.017*"войско" + 0.015*"полка" + 0.015*"стрелковый" + 0.015*"военный"'

In [75]:
lda_5.print_topic(64) # Спортивные соревнования

'0.027*"клуб" + 0.026*"чемпионат" + 0.022*"команда" + 0.022*"турнир" + 0.022*"матч" + 0.021*"сезон" + 0.015*"кубок" + 0.014*"мир" + 0.012*"чемпион" + 0.011*"игрок"'

In [76]:
lda_5.print_topic(41) # География, морская тематика

'0.134*"остров" + 0.030*"азербайджан" + 0.030*"архипелаг" + 0.023*"экспедиция" + 0.021*"пролив" + 0.019*"вод" + 0.017*"морской" + 0.016*"мыс" + 0.014*"полярный" + 0.014*"залив"'

## 8) в отдельной ячейке сравните лучшую модель без tfidf и лучшую модель с tfidf (приведите несколько тем, которые стали лучше или хуже, или которых раньше вообще не было; можно привести значения перплексии и когерентности для обеих моделей)

In [77]:
metrics(lda_3, corpus, texts)

Перплексия -11.24918626658083, когерентность 0.5814369616350556


In [78]:
metrics(lda_5, corpus_tfidf, texts)

Перплексия -31.660234840719102, когерентность 0.4537931140055324


По значениям метрик модель без tf-idf должна быть лучше, но по рассмотренным ниже темам мне кажется, что модель с tf-idf справилась лучше

In [84]:
lda_3.print_topic(57) # Спортивные соревнования

'0.029*"клуб" + 0.027*"команда" + 0.023*"матч" + 0.021*"чемпионат" + 0.020*"сезон" + 0.014*"кубок" + 0.012*"мир" + 0.012*"сборный" + 0.010*"состав" + 0.009*"выступать"'

In [85]:
lda_5.print_topic(64) # Спортивные соревнования - кажется, что модель с tfidf справилась лучше с этой темой

'0.027*"клуб" + 0.026*"чемпионат" + 0.022*"команда" + 0.022*"турнир" + 0.022*"матч" + 0.021*"сезон" + 0.015*"кубок" + 0.014*"мир" + 0.012*"чемпион" + 0.011*"игрок"'

In [86]:
lda_3.print_topic(11) # Морская тема - выражена четче у модели без tfidf, уклон в сторону судоходства 

'0.033*"корабль" + 0.025*"флот" + 0.013*"состав" + 0.012*"лодка" + 0.010*"морской" + 0.010*"судно" + 0.008*"подводный" + 0.008*"капитан" + 0.008*"флотилия" + 0.007*"1"'

In [87]:
lda_5.print_topic(41) # Морская тема - уклон в сторону географических сущностей, а не кораблей/флота и т.д.

'0.134*"остров" + 0.030*"азербайджан" + 0.030*"архипелаг" + 0.023*"экспедиция" + 0.021*"пролив" + 0.019*"вод" + 0.017*"морской" + 0.016*"мыс" + 0.014*"полярный" + 0.014*"залив"'

In [89]:
lda_3.print_topic(45) # Армия/война(с уклоном на ВОВ из-за августа, июля и 1941)

'0.024*"дивизия" + 0.016*"август" + 0.015*"орден" + 0.013*"июль" + 0.013*"1941" + 0.011*"назначить" + 0.011*"военный" + 0.011*"корпус" + 0.009*"стрелковый" + 0.009*"начальник"'

In [90]:
lda_5.print_topic(34) # Армия/война - кажется, что модель с tf-idf справилась лучше с данной темой

'0.028*"армия" + 0.023*"дивизия" + 0.020*"командир" + 0.019*"бой" + 0.017*"фронт" + 0.017*"война" + 0.017*"войско" + 0.015*"полка" + 0.015*"стрелковый" + 0.015*"военный"'

## 9) проделайте такие же действия для NMF (образец в конце тетрадки), для построения словаря воспользуйтесь возможностями Count или Tfidf Vectorizer (попробуйте другие значение max_features, min_df, max_df, сделайте нграмы через ngram_range, если хватает памяти), попробуйте такие же количества тем

In [93]:
from sklearn.decomposition import NMF
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
import pandas as pd

In [94]:
stexts = [' '.join(text) for text in texts]

In [101]:
def NMF_fit(vectorizer, stexts, n_components):
    X = vectorizer.fit_transform(stexts)
    # n_components - главный параметр в NMF, это количество тем. 
    # Если данных много, то увеличения этого параметра сильно увеличивает время обучения
    model = NMF(n_components=n_components)
    model.fit(X)
    pd.set_option('display.max_columns', n_components)
    pd.set_option('display.max_rows', n_components)
    feat_names = vectorizer.get_feature_names()    
        
    print(f"Метрика: {model.reconstruction_err_}")
    return model

In [103]:
vectorizer_1 = TfidfVectorizer(max_features=2000, min_df=10, max_df=0.1, ngram_range=(1,2))
model_1 = NMF_fit(vectorizer_1, stexts, 100)

Метрика: 75.53788669153192


In [105]:
vectorizer_2 = TfidfVectorizer(max_features=1000, min_df=10, max_df=0.1, ngram_range=(1,2))
model_2 = NMF_fit(vectorizer_2, stexts, 100)

Метрика: 70.47144359940324


In [106]:
vectorizer_3 = TfidfVectorizer(max_features=500, min_df=10, max_df=0.1, ngram_range=(1,2))
model_3 = NMF_fit(vectorizer_3, stexts, 100)

Метрика: 63.5343212978676


In [110]:
vectorizer_4 = TfidfVectorizer(max_features=500, min_df=20, max_df=0.1, ngram_range=(1,2))
model_4 = NMF_fit(vectorizer_4, stexts, 100)

Метрика: 63.362673221864846


In [136]:
vectorizer_5 = TfidfVectorizer(max_features=500, min_df=20, max_df=0.2, ngram_range=(1,2))
model_5 = NMF_fit(vectorizer_5, stexts, 100)

Метрика: 61.42584501592593


In [117]:
vectorizer_6 = TfidfVectorizer(max_features=500, min_df=20, max_df=0.25, ngram_range=(1,2))
model_6 = NMF_fit(vectorizer_6, stexts, 100)

Метрика: 61.313508697056


Лучшая модель для TfidfVectorizer по метрике model_6 (61.313508697056)

In [107]:
vectorize_cv_1 = CountVectorizer(max_features=2000, min_df=10, max_df=0.1, ngram_range=(1,2))
model_cv_1 = NMF_fit(vectorize_cv_1, stexts, 100)

Метрика: 1152.637703159999


In [108]:
vectorize_cv_2 = CountVectorizer(max_features=1000, min_df=10, max_df=0.1, ngram_range=(1,2))
model_cv_2 = NMF_fit(vectorize_cv_2, stexts, 100)

Метрика: 959.3710449321155


In [109]:
vectorize_cv_3 = CountVectorizer(max_features=500, min_df=10, max_df=0.1, ngram_range=(1,2))
model_cv_3 = NMF_fit(vectorize_cv_3, stexts, 100)

Метрика: 736.4074390562737


In [111]:
vectorize_cv_4 = CountVectorizer(max_features=500, min_df=20, max_df=0.1, ngram_range=(1,2))
model_cv_4 = NMF_fit(vectorize_cv_4, stexts, 100)

Метрика: 736.3983748525983


In [114]:
vectorize_cv_5 = CountVectorizer(max_features=500, min_df=20, max_df=0.2, ngram_range=(1,2))
model_cv_5 = NMF_fit(vectorize_cv_5, stexts, 100)

Метрика: 777.924378342069


In [116]:
vectorize_cv_6 = CountVectorizer(max_features=500, min_df=20, max_df=0.08, ngram_range=(1,2))
model_cv_6 = NMF_fit(vectorize_cv_6, stexts, 100)

Метрика: 695.4627169447322


Лучшая модель для CountVectorizer по метрике model_cv_6 (695.4627169447322). Сравню их по темам

In [124]:
def print_topics(model, vectorizer):
    feat_names = vectorizer.get_feature_names()
    top_words = model.components_.argsort()[:,:-5:-1]

    for i in range(top_words.shape[0]):
        words = [feat_names[j] for j in top_words[i]]
        print(i, "--".join(words))
        
def print_topic(i, model, vectorizer):
    feat_names = vectorizer.get_feature_names()
    top_words = model.components_.argsort()[:,:-5:-1]

    words = [feat_names[j] for j in top_words[i]]
    print(i, "--".join(words))

In [121]:
print_topics(model_6, vectorizer_6)

0 житомирский--код--житомирский область--район житомирский
1 летний олимпийский--летний--олимпийский--олимпийский игра
2 весь--день--самый--однако
3 сесть--течение--сельский--код коатуа
4 вид--некоторый--например--около
5 матч--провести--против--сборный
6 зимний олимпийский--зимний--олимпийский--олимпийский игра
7 фильм--американский--состояться--выйти
8 хутор--сельский--входить--иметься
9 альбом--выпустить--выйти--стать
10 июнь--октябрь--март--ноябрь
11 остров--относиться--земля--небольшой
12 уезд--городской--губерния--специальный
13 граф--ii--де--смерть
14 город--население--городской--округа
15 армия--войско--дивизия--фронт
16 название--пункт--украина--различный
17 турнир--финал--международный--счёт
18 центр--административный--население--провинция
19 дом--здание--проект--построить
20 улица--москва--бывший--иметься
21 церковь--храм--николай--построить
22 состав--входить--войти--области
23 европа--центральный--северный--ул
24 мочь--использовать--использоваться--случай
25 род--входить--

In [127]:
print_topic(15, model_6, vectorizer_6) # Армия

15 армия--войско--дивизия--фронт


In [130]:
print_topic(34, model_6, vectorizer_6) # Музыкальная группа

34 группа--участник--играть--музыкальный


In [131]:
print_topic(84, model_6, vectorizer_6) # Семья

84 сын--брат--отец--дочь


In [123]:
print_topics(model_cv_6, vectorize_cv_6)

0 подвеска--автомобиль--ход--сила
1 войско--фронт--армия--го
2 власть--государство--право--сторона
3 матч--против--провести--сыграть
4 of--2010--2010 год--2011
5 уезд--городской--специальный--округ
6 экспедиция--северный--южный--план
7 дивизия--1941--1941 год--стрелковый
8 ребёнок--состояние--образ--жизнь
9 брак--право--пара--ребёнок
10 раунд--выйти--смочь--финал
11 сын--брат--дочь--жена
12 армия--войско--сила--дивизия
13 доктор--серия--сезон--возраст
14 корабль--морской--ход--главный
15 самолёт--установить--модель--высота
16 китайский--отец--друг--отношение
17 фильм--режиссёр--герой--главный
18 альбом--выпустить--выйти--позиция
19 партия--политический--программа--движение
20 орден--должность--начальник--назначить
21 марка--сделать--выпустить--чёрный
22 титул--чемпион--победа--проиграть
23 вода--программа--москва--2010
24 деревня--двор--губерния--житель
25 сборный--сборная--кубок--победа
26 общество--развитие--деятельность--далее
27 компания--деятельность--международный--крупный
28 соц

In [132]:
print_topic(11, model_cv_6, vectorize_cv_6) # Семья

11 сын--брат--дочь--жена


In [133]:
print_topic(12, model_cv_6, vectorize_cv_6) # Армия

12 армия--войско--сила--дивизия


In [134]:
print_topic(17, model_cv_6, vectorize_cv_6) # Кино

17 фильм--режиссёр--герой--главный


Из двух моделей NMF лучшей получилась модель для TfidfVectorizer (и по метрикам, и по темам). Мне кажется, обе модели NMF показали себя лучше чем LDA, если смотреть по темам. Интересно, что модели с tf-idf (и NMF, и LDA) показали себя лучше, чем модели без. 